In [1]:
!pip install transformers


In [6]:
with open('data.txt', 'r') as file:
    data = file.read()
print(data)

Yudu Robotics
Yudurobotics is a product innovation company based in Bangalore, that focuses on developing high quality robotic products for education and other sectors. We’ve been pioneering in the world of robotics for over 12 years, crafting high-quality robotic products and educational tools that bring technology to life. Our flagship software, PLODE, ties it all together, creating a universal platform for controlling everything from our beginner-friendly kits to advanced robotics. We cater to a wide range, offering STEM kits for the curious minds of 5-year-olds to the ambitious projects of 22-year-olds. Our mission is simple: make learning robotics engaging, accessible, and above all, fun. From humanoid robots and all-terrain bots to precision tools like 3D printers and laser engravers, we’re like a robotics candy shop: a sweet spot for educators, hobbyists, and enthusiasts. So whether you're a teacher, a parent, or a curious soul looking to explore robotics, Yudu Robotics has got 

In [8]:
!pip install spacy
!python -m spacy download en_core_web_sm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 4.3 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 634.7/634.7 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 761.0/761.0 kB 9.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 9.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.4/5.4 MB 11.8 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 18.2 MB/s eta 0:00:00a 0:00:01
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [ ]:
import spacy

# Increase the max_length limit
nlp = spacy.load("en_core_web_sm")
nlp.max_length = 5000000  # Set a higher limit


In [ ]:
def extract_advanced_relationships(text):
    doc = nlp(text)
    entities = {ent.text: ent.label_ for ent in doc.ents}
    relationships = []

    for token in doc:
        if token.dep_ == "ROOT":
            subject = None
            object_ = None

            for child in token.children:
                if child.dep_ == "nsubj":  # Subject
                    subject = " ".join([t.text for t in child.subtree])
                if child.dep_ in ["dobj", "attr"]:  # Direct Object
                    object_ = " ".join([t.text for t in child.subtree])
                if child.dep_ == "prep":  # Prepositional Object
                    for subchild in child.children:
                        if subchild.dep_ in ["pobj"]:
                            object_ = " ".join([t.text for t in subchild.subtree])

            if subject and object_:
                relationships.append((subject, token.text, object_))

    return list(entities.items()), relationships


In [ ]:
from spacy.matcher import Matcher

matcher = Matcher(nlp.vocab)
pattern = [{"LOWER": "ceo"}, {"LOWER": "of"}, {"ENT_TYPE": "ORG"}]
matcher.add("CEO_PATTERN", [pattern])

doc = nlp("Elon Musk is the CEO of Tesla.")
matches = matcher(doc)

for match_id, start, end in matches:
    print(doc[start:end]) 

In [15]:
text = data#"Google acquired YouTube in 2006. Tesla is led by Elon Musk. OpenAI developed ChatGPT."
entities, relationships = extract_advanced_relationships(text)

print("Entities:", entities)
print("Relationships:")
for r in relationships:
    print(f"{r[0]} --[{r[1]}]--> {r[2]}")


Entities: [('Yudu Robotics\nYudurobotics', 'PERSON'), ('Bangalore', 'PERSON'), ('over 12 years', 'DATE'), ('5-year-olds', 'DATE'), ('22-year-olds', 'DATE'), ('Yudu Robotics', 'PERSON'), ('one', 'CARDINAL'), ('Yudurobotics', 'ORG'), ('two', 'CARDINAL'), ('Hardware', 'ORG'), ('Software', 'ORG'), ('STEM', 'ORG'), ('jumpstart', 'NORP'), ('Hardware Products', 'ORG'), ('Codable Electronics Kit', 'ORG'), ('Basic Electronics Kit', 'ORG'), ('Animatronics Kit', 'ORG'), ('Robotics Kit', 'PERSON'), ('Rapid Prototyping Tools', 'ORG'), ('Port 11', 'EVENT'), ('HARDWARE Products\nDive', 'ORG'), ('Codable Electronics Kits', 'ORG'), ('Basic Electronics Kits', 'WORK_OF_ART'), ('Animatronics Kits', 'PERSON'), ('Robotics Kits', 'PERSON'), ('Codable Electronics Kit\nOur Codable Electronics Kits', 'ORG'), ('10 to 16', 'DATE'), ('PeeCee Compute', 'ORG'), ('PeeCee', 'ORG'), ('Roboki', 'PERSON'), ('Playdynamex', 'ORG'), ('This Single Robotic Board', 'ORG'), ('SRB', 'ORG'), ('Single Board Computer', 'ORG'), ('To

In [16]:
!pip install neo4j

python(11304) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.


In [ ]:
from neo4j import GraphDatabase

driver = GraphDatabase.driver("neo4j+s://7b471d17.databases.neo4j.io", auth=("neo4j", ""))

def store_in_neo4j(tx, entity, label):
    tx.run("MERGE (e:Entity {name: $name, type: $label})", name=entity, label=label)

def store_relationship(tx, subject, relation, object_):
    tx.run("""
    MATCH (a:Entity {name: $subject})
    MATCH (b:Entity {name: $object_})
    MERGE (a)-[:RELATION {type: $relation}]->(b)
    """, subject=subject, relation=relation, object_=object_)

with driver.session() as session:
    for entity, label in entities:
        session.execute_write(store_in_neo4j, entity, label)

    for subject, relation, object_ in relationships:
        session.execute_write(store_relationship, subject, relation, object_)


KeyboardInterrupt: 

In [ ]:
import openai
from neo4j import GraphDatabase

# Neo4j connection setup
driver = GraphDatabase.driver(
    "neo4j+s://7b471d17.databases.neo4j.io", 
    auth=("neo4j", "")
)

# OpenAI API setup
openai.api_key = "YOUR_OPENAI_API_KEY"

def generate_cypher_query(prompt):
    """Uses OpenAI LLM to generate Cypher queries from natural language."""
    response = openai.ChatCompletion.create(
        model="gpt-4",  # Use GPT-4 for better reasoning
        messages=[{"role": "system", "content": "You are an AI that converts natural language to Cypher queries."},
                  {"role": "user", "content": prompt}]
    )
    cypher_query = response["choices"][0]["message"]["content"]
    return cypher_query

def query_neo4j(cypher_query):
    """Executes a Cypher query and retrieves the result."""
    with driver.session() as session:
        result = session.run(cypher_query)
        return [record.data() for record in result]

# Example Natural Language Query
user_input = "Find all entities connected to 'Elon Musk'"

# Generate Cypher Query using LLM
cypher_query = generate_cypher_query(f"Convert this to Cypher: {user_input}")

# Execute Query on Neo4j
result = query_neo4j(cypher_query)

print("Generated Query:\n", cypher_query)
print("Query Result:\n", result)
